In [8]:
import numpy as np
from math import log
from loadMnist import load_images, load_labels

In [9]:
# 讀資料
train_data  = load_images("data/train-images.idx3-ubyte")
train_label = load_labels("data/train-labels.idx1-ubyte")
test_data   = load_images("data/t10k-images.idx3-ubyte")
test_label  = load_labels("data/t10k-labels.idx1-ubyte")

# 目標: 紀錄各label機率(P(0),P(1),....)
# 1.創一個字典，紀錄各label數量
label_number_dict = {}
for label in train_label:
    if label in label_number_dict:
        label_number_dict[label] += 1
    else:
        label_number_dict[label] = 1
print("label_number_dict: ", label_number_dict)


# 2. 創一個字典，紀錄各label機率(P(0),P(1),....)
label_probability_dict = {}
for label in label_number_dict:
    label_probability_dict[label] = label_number_dict[label] / len(train_data)
print("label_probability_dict: ", label_probability_dict)

label_number_dict:  {5: 5421, 0: 5923, 4: 5842, 1: 6742, 9: 5949, 2: 5958, 3: 6131, 6: 5918, 7: 6265, 8: 5851}
label_probability_dict:  {5: 0.09035, 0: 0.09871666666666666, 4: 0.09736666666666667, 1: 0.11236666666666667, 9: 0.09915, 2: 0.0993, 3: 0.10218333333333333, 6: 0.09863333333333334, 7: 0.10441666666666667, 8: 0.09751666666666667}


In [3]:
# 目標: 算個別條件機率，例:P(第一格,暗淡=10|label=0)=0.05,P(第一格,暗淡=8|label=0)=0.05,...,P(第七八四格,暗淡=30|lebel=9)=0.01
# 1.創一個三維 數量 矩陣儲存結果[10*784*32]
number3D = np.zeros((10, 784, 32))
for i, label in enumerate(train_label):
    for k, pixel in enumerate(train_data[i]):
         # pixel_range代表黑色(0~32)淡深程度
        pixel_range = pixel // 8
        number3D[label][k][pixel_range] += 1  
    
print(number3D[5])  

[[5421.    0.    0. ...    0.    0.    0.]
 [5421.    0.    0. ...    0.    0.    0.]
 [5421.    0.    0. ...    0.    0.    0.]
 ...
 [5421.    0.    0. ...    0.    0.    0.]
 [5421.    0.    0. ...    0.    0.    0.]
 [5421.    0.    0. ...    0.    0.    0.]]


In [4]:
# 2.創一個三維 條件機率 矩陣儲存結果[10*784*32]，例:label9 在第四格 是 淡黑(29)的機率
condiction_probability3D = np.zeros((10, 784, 32), dtype=float)
for label in range(10):
    for i in range(784):
        condiction_probability3D[label][i] = number3D[label][i] / label_number_dict[label]

In [6]:
# 進行test資料集，離散版本運算
error = 0
for j in range(len(test_data)):
    prob_sum = 0
    prob_logs = []
    for label in range(10):
        prob_log = 0
        for i, pixel in enumerate(test_data[j]):  
            pixel_range = pixel // 8
            prob_log += log(max(1e-125, condiction_probability3D[label][i][pixel_range]))  # log x越接近0,y越接近負無限大,又因為log0不存在，所以將機率0設定一個非常接近零的數值當屏障 

        prob_logs.append(prob_log + log(label_probability_dict[label]))    # 最後要乘P(label)的機率!
        prob_sum += prob_log + log(label_probability_dict[label])
    
    # 印出結果 #
    print("Postirior (in log scale):")
    log_result = np.array(prob_logs)/prob_sum
    for i, v in enumerate(log_result):
        print("{}: {}".format(i, v))
    pred = np.argmin(log_result)         # 因為開log，所以要選最小的才是機率最高的
    ans  = test_label[j] 
    print("Prediction: {}, Ans: {}".format(pred, ans))
    print()
    if pred != ans:
        error += 1
    
# 計算錯誤率 #
error_rate = error/len(test_data)
print("Error rate: {}".format(error_rate))


Postirior (in log scale):
0: 0.11882903481484355
1: 0.24674896848621786
2: 0.13090740258513447
3: 0.07349471372766876
4: 0.07151801227003549
5: 0.058742390014145884
6: 0.20370057755417897
7: 0.023442847325935837
8: 0.045463170001416996
9: 0.02715288322042213
Prediction: 7, Ans: 7

Postirior (in log scale):
0: 0.09217799369274232
1: 0.12224761774738913
2: 0.02465377914892282
3: 0.07589659217532724
4: 0.10117183925986431
5: 0.06927975730780445
6: 0.061554898406704195
7: 0.1956654054181017
8: 0.09139922687238469
9: 0.16595288997075913
Prediction: 2, Ans: 2

Postirior (in log scale):
0: 0.09734189537058244
1: 0.04797709323522007
2: 0.07438336895365188
3: 0.0758913711588617
4: 0.07806130409085837
5: 0.07284540759096383
6: 0.07803511907410253
7: 0.22393389989404963
8: 0.07566718959786584
9: 0.1758633510338438
Prediction: 1, Ans: 1

Postirior (in log scale):
0: 0.03851706529485013
1: 0.4242620873770465
2: 0.04818971124641522
3: 0.047934284535731286
4: 0.06906557208772454
5: 0.0459987073276569

Prediction: 2, Ans: 2

Postirior (in log scale):
0: 0.12506364479629353
1: 0.30444662238557296
2: 0.08722635041386513
3: 0.06342232325225534
4: 0.03871978338748269
5: 0.06352223747893629
6: 0.15949310611286413
7: 0.02254359969471664
8: 0.09868288781206072
9: 0.03687944466595242
Prediction: 7, Ans: 7

Postirior (in log scale):
0: 0.11777885544095273
1: 0.062301123297558075
2: 0.09431594862954386
3: 0.08760626208444708
4: 0.08979418833292725
5: 0.0830092145509468
6: 0.2080163559298238
7: 0.08521284217222018
8: 0.08668714452596529
9: 0.08527806503561498
Prediction: 1, Ans: 1

Postirior (in log scale):
0: 0.051447386156198656
1: 0.29701336518619026
2: 0.046823160148495024
3: 0.04611462278583931
4: 0.055677824052829124
5: 0.04745110919649211
6: 0.06920865565697928
7: 0.1383309563180109
8: 0.06913961653621262
9: 0.17879330396275284
Prediction: 3, Ans: 2

Postirior (in log scale):
0: 0.09952061988720326
1: 0.05246654375641721
2: 0.07780569778657105
3: 0.07465283845095533
4: 0.0835915788668633

Postirior (in log scale):
0: 0.027071364499118213
1: 0.49656238067453246
2: 0.03282943250539073
3: 0.10251745160626162
4: 0.04647442846913466
5: 0.032371776850966504
6: 0.043930381411292796
7: 0.04727368317326473
8: 0.04609281501895514
9: 0.12487628579108317
Prediction: 0, Ans: 0

Postirior (in log scale):
0: 0.10301672947674659
1: 0.2492736286164466
2: 0.09285249456191397
3: 0.06896411579858822
4: 0.05751361362163859
5: 0.08020031917560737
6: 0.19088661739454588
7: 0.019967612198491188
8: 0.059185031708316786
9: 0.07813983744770497
Prediction: 7, Ans: 7

Postirior (in log scale):
0: 0.023837703943631446
1: 0.5215409769345103
2: 0.03177076646263606
3: 0.06501554859799116
4: 0.04577953841618395
5: 0.031224610898870197
6: 0.04385285756815107
7: 0.10254217217558234
8: 0.03321366483763367
9: 0.10122216016480967
Prediction: 0, Ans: 0

Postirior (in log scale):
0: 0.036992352350848835
1: 0.22649361902062476
2: 0.035019272559016795
3: 0.03629312518729019
4: 0.042801691370944694
5: 0.038316193

Postirior (in log scale):
0: 0.07514556005209926
1: 0.26287537279128403
2: 0.028775703741421292
3: 0.06403147581196879
4: 0.08286239355664465
5: 0.07389455152871689
6: 0.026817656549930426
7: 0.14007272819826194
8: 0.10663352131822189
9: 0.13889103645145068
Prediction: 6, Ans: 6

Postirior (in log scale):
0: 0.04517325216794554
1: 0.4270332730673999
2: 0.05648934783034368
3: 0.07461448553251658
4: 0.05657620486592282
5: 0.05132891309960867
6: 0.11454186546455639
7: 0.06172642524542837
8: 0.0541540402012673
9: 0.058362192525010875
Prediction: 0, Ans: 0

Postirior (in log scale):
0: 0.10703520924072221
1: 0.25010391218316996
2: 0.12388176595633156
3: 0.06436816271478886
4: 0.038159570735091415
5: 0.03415071143221175
6: 0.24487440844814942
7: 0.03712854088385158
8: 0.036950727044631176
9: 0.06334699136105232
Prediction: 5, Ans: 5

Postirior (in log scale):
0: 0.06590906197500039
1: 0.3972048706133713
2: 0.04124960722732537
3: 0.03206188939492115
4: 0.0249096566429316
5: 0.0533265203484038

4: 0.04093181651166386
5: 0.05481004801705024
6: 0.032706381077240235
7: 0.22112668940522578
8: 0.07105958242712937
9: 0.153696955521866
Prediction: 6, Ans: 6

Postirior (in log scale):
0: 0.053564600942260655
1: 0.225080596493565
2: 0.05463805396702237
3: 0.04919180503349322
4: 0.061121626384500985
5: 0.04838713643814511
6: 0.05360210849180069
7: 0.21669040017083024
8: 0.05168646136439375
9: 0.1860372107139877
Prediction: 5, Ans: 5

Postirior (in log scale):
0: 0.10166989623259672
1: 0.212632458861377
2: 0.039883599259129536
3: 0.04388975847445916
4: 0.04064033148566944
5: 0.08029660046431362
6: 0.13172304159508857
7: 0.07437176273313112
8: 0.0941509740637573
9: 0.18074157683047742
Prediction: 2, Ans: 7

Postirior (in log scale):
0: 0.089402177769513
1: 0.11739899163458077
2: 0.0805143924143018
3: 0.07685823444635231
4: 0.08013593132521604
5: 0.07444371047561006
6: 0.18673574359682704
7: 0.11698140613199375
8: 0.06630846648800112
9: 0.11122094571760407
Prediction: 8, Ans: 8

Postirior

...

Postirior (in log scale):
0: 0.1145257358292119
1: 0.2403372568353617
2: 0.14894150557647076
3: 0.07540699491937228
4: 0.052076744924313675
5: 0.03559490226830305
6: 0.20404241158702272
7: 0.02694001842900935
8: 0.07265948918505864
9: 0.029474940445875793
Prediction: 7, Ans: 7

Postirior (in log scale):
0: 0.043759933763543625
1: 0.218638867141503
2: 0.045461651945979745
3: 0.03976573186526713
4: 0.09022096148898262
5: 0.042534447021261135
6: 0.07045224066418776
7: 0.22056963142831001
8: 0.04507407829394809
9: 0.18352245638701697
Prediction: 3, Ans: 3

Postirior (in log scale):
0: 0.05067272802153802
1: 0.3817007362357444
2: 0.07009951485467383
3: 0.07605467155028175
4: 0.04244373650307345
5: 0.04836266100627932
6: 0.10788553302578616
7: 0.08772867900549405
8: 0.049203427888498956
9: 0.08584831190862995
Prediction: 4, Ans: 4

Postirior (in log scale):
0: 0.08868285485066801
1: 0.10676215152996145
2: 0.053277361268101814
3: 0.07848912772123627
4: 0.08041020843280386
5: 0.077642441206172

Postirior (in log scale):
0: 0.10301494858764633
1: 0.36149444671359177
2: 0.09998058235483391
3: 0.053494159903378455
4: 0.049294683950102954
5: 0.05162685418183747
6: 0.1453417435994223
7: 0.0341545346245188
8: 0.06764537882282647
9: 0.03395266726184136
Prediction: 9, Ans: 9

Postirior (in log scale):
0: 0.07743080837437848
1: 0.09423164671634256
2: 0.06649417661079197
3: 0.06685655327279863
4: 0.06626019957837129
5: 0.06166597079340934
6: 0.06457100279683174
7: 0.31318440446177664
8: 0.062092257288950195
9: 0.12721298010634915
Prediction: 5, Ans: 8

Postirior (in log scale):
0: 0.08180709303225137
1: 0.08362640924718535
2: 0.07680883658620205
3: 0.0755125231992993
4: 0.08017795220147592
5: 0.0727767106209864
6: 0.23970635347801056
7: 0.14344783071877323
8: 0.06787351338589503
9: 0.07826277752992077
Prediction: 8, Ans: 2

Postirior (in log scale):
0: 0.13375244267571226
1: 0.14475999757837685
2: 0.14676722257681346
3: 0.09286878398266697
4: 0.07146421112938992
5: 0.07182094876331566


Postirior (in log scale):
0: 0.07994878042485327
1: 0.0465441342460192
2: 0.05855143897508403
3: 0.06412742742501319
4: 0.06596227347172841
5: 0.06172816085287762
6: 0.17709931592966416
7: 0.24709546438704508
8: 0.05857920802668524
9: 0.14036379626102993
Prediction: 1, Ans: 1

Postirior (in log scale):
0: 0.09308257715778698
1: 0.31826257909432637
2: 0.10157932476609405
3: 0.10230753880747863
4: 0.06041667187197836
5: 0.05403169565622607
6: 0.13955306362732936
7: 0.030761163942747607
8: 0.06219895542323925
9: 0.0378064296527934
Prediction: 7, Ans: 9

Postirior (in log scale):
0: 0.055709809478101724
1: 0.15690728463943632
2: 0.0478683445522854
3: 0.0719945490441272
4: 0.11170056911054634
5: 0.048709091208666296
6: 0.15658627721175583
7: 0.13134816748692493
8: 0.08799573868503714
9: 0.13118016858311884
Prediction: 2, Ans: 3

Postirior (in log scale):
0: 0.07999686839201156
1: 0.10516087676843887
2: 0.07437309317106876
3: 0.10205781015580559
4: 0.08961076246148923
5: 0.03549216082174137


Postirior (in log scale):
0: 0.08434035451213084
1: 0.1855695275547093
2: 0.03365386560059919
3: 0.08106156049315001
4: 0.06325517081738713
5: 0.06404451174251553
6: 0.028782419413482994
7: 0.19930487378683645
8: 0.09309721649492292
9: 0.16689049958426555
Prediction: 6, Ans: 6

Postirior (in log scale):
0: 0.029462566854522226
1: 0.4210313240582626
2: 0.03513147495089972
3: 0.03328655097739393
4: 0.08521694342073174
5: 0.03161861043186098
6: 0.19694342499931014
7: 0.04693513680025362
8: 0.04432455167145952
9: 0.07604941583530543
Prediction: 0, Ans: 0

Postirior (in log scale):
0: 0.11360219378570019
1: 0.23097207304247933
2: 0.13105864918135418
3: 0.08167382528892407
4: 0.04785741348600027
5: 0.047684326087309124
6: 0.21120619267454205
7: 0.02592196453145471
8: 0.08094769574481192
9: 0.029075666177423937
Prediction: 7, Ans: 7

Postirior (in log scale):
0: 0.029535471842703012
1: 0.28560541847562865
2: 0.034467388354064404
3: 0.044716516914094194
4: 0.0926416829354746
5: 0.0425643272525

Postirior (in log scale):
0: 0.06628510706198809
1: 0.4292175943327841
2: 0.08587503474806814
3: 0.04931766548064688
4: 0.03897123237454588
5: 0.04485192376205502
6: 0.15777795681605009
7: 0.043544250373268194
8: 0.04533245825508455
9: 0.0388267767955091
Prediction: 9, Ans: 9

Postirior (in log scale):
0: 0.02504181786862955
1: 0.43521902610817903
2: 0.04136591101913878
3: 0.0801759403921014
4: 0.061982138141265006
5: 0.0297766893759932
6: 0.09967765631804631
7: 0.08494321166857037
8: 0.030302910739019924
9: 0.11151469836905635
Prediction: 0, Ans: 0

Postirior (in log scale):
0: 0.10485742408059513
1: 0.05116457529875246
2: 0.0755660884439845
3: 0.07982834661918538
4: 0.08753054785571757
5: 0.07861899301043666
6: 0.12996224824995106
7: 0.23311528712732543
8: 0.07410930814898112
9: 0.08524718116507064
Prediction: 1, Ans: 1

Postirior (in log scale):
0: 0.051902038034722785
1: 0.18563396848325123
2: 0.036906152184373375
3: 0.043665520822564745
4: 0.0735010007798232
5: 0.04775930343193579

In [7]:
print("Imagination of numbers in Bayesian classifier: ")
for label in range(10):
    temp = []
    for pixels in condiction_probability3D[label]:
        max_pixel_range_index = np.argmax(pixels)  # 選出淡到黑機率最大的pixel_range index
        if max_pixel_range_index >= 16:            # 因為>=128("16"*8)是1(黑) 
            temp.append(1)
        else:
            temp.append(0)
    
    # 印出數字 #
    print("{}:".format(label))
    for i in range(len(temp)):
        if i != 0 and i % 28 == 0:
            print()
        print(temp[i], end="")
    print()

Imagination of numbers in Bayesian classifier: 
0:
0000000000000000000000000000
0000000000000000000000000000
0000000000000000000000000000
0000000000000000000000000000
0000000000000000000000000000
0000000000000001110000000000
0000000000000111111100000000
0000000000001111111110000000
0000000000011111111110000000
0000000000111110001111000000
0000000001111000000111000000
0000000001110000000011100000
0000000011100000000011100000
0000000111100000000011100000
0000000111000000000011100000
0000000111000000000011000000
0000001110000000000111000000
0000001110000000000110000000
0000001110000000001110000000
0000001111000000111100000000
0000000111110011111000000000
0000000111111111110000000000
0000000011111111000000000000
0000000000111100000000000000
0000000000000000000000000000
0000000000000000000000000000
0000000000000000000000000000
0000000000000000000000000000
1:
0000000000000000000000000000
0000000000000000000000000000
0000000000000000000000000000
0000000000000000000000000000
000000000000000000